# to run this notebook
```
conda create -n test kwant adaptive dask_jobqueue
```

In [18]:
import adaptive
from distributed import Client
import sympy
adaptive.notebook_extension()
print(sympy.__version__)

'1.4'

In [1]:
from dask_jobqueue import SLURMCluster

cluster = SLURMCluster(
    cores=8,
    processess=8,
    memory="16GB",
    project="wal",
    walltime="10:00:00",
    queue="debug",
    local_directory='TMPDIR',
    log_directory='TMPDIR',
    env_extra=[
        "export MKL_NUM_THREADS=1",
        "export OPENBLAS_NUM_THREADS=1",
        "export OMP_NUM_THREADS=1",
        "export SYMPY_USE_CACHE=no",
    ],
)

/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/dask_jobqueue/config.py:12: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)
/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/distributed/deploy/local.py:106: UserWarning: diagnostics_port has been deprecated. Please use `dashboard_address=` instead
  "diagnostics_port has been deprecated. "


In [2]:
cluster

In [14]:
cluster.scale(100)

In [4]:
client = Client(cluster)

In [10]:
def get_template(subs=None):
    import kwant
    import kwant.continuum
    if subs is None:
        subs = {}
    ham = ("(0.5 * hbar**2 * (k_x**2 + k_y**2 + k_z**2) / m_eff - mu + V) * kron(sigma_0, sigma_z) + "
           "alpha * (k_y * kron(sigma_x, sigma_z) - k_x * kron(sigma_y, sigma_z)) + "
           "0.5 * g * mu_B * (B_x * kron(sigma_x, sigma_0) + B_y * kron(sigma_y, sigma_0) + B_z * kron(sigma_z, sigma_0)) + "
           "Delta * kron(sigma_0, sigma_x)")
    template = kwant.continuum.discretize(ham, locals=subs)
    return template

def f(x):
    from time import sleep
    from random import random
    sleep(random() / 10)
    get_template({'V': 0})
    sleep(random() / 10)
    get_template({'Delta': 0, 'V': 0})
    return 1

learner = adaptive.Learner2D(f, [[-1, 1], [-1, 1]])
runner = adaptive.Runner(learner, executor=client, log=True)
runner.live_info()

In [17]:
runner.task.print_stack()

Traceback for <Task finished coro=<AsyncRunner._run() done, defined at /w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py:545> exception=RuntimeError('An error occured while evaluating "learner.function((-0.43209876543209874, 0.16049382716049382))". See the traceback for details.:\n\nTraceback (most recent call last):\n  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 196, in _process_futures\n    y = fut.result()\n  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/distributed/cfexecutor.py", line 32, in _cascade_future\n    six.reraise(*result)\n  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/six.py", line 692, in reraise\n    raise value.with_traceback(tb)\n  File "<ipython-input-10-e1c11dc56422>", line 17, in f\n    get_template({\'V\': 0})\n  File "<ipython-input-10-e1c11dc56422>", line 10, in get_template\n    template = kwant.continuum.discretize(ham, locals=su

  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 501, in status
    return 'failed'
  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 501, in status
    return 'failed'
  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 562, in _run
    self._cleanup()
  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 204, in _process_futures
    self._do_raise(e, x)
  File "/w2scratch/home/t-banij/miniconda3/lib/python3.7/site-packages/adaptive/runner.py", line 153, in _do_raise
    ) from e
